## Overview

This notebook will show you how to create and query a table or DataFrame that you uploaded to DBFS. [DBFS](https://docs.databricks.com/user-guide/dbfs-databricks-file-system.html) is a Databricks File System that allows you to store data for querying inside of Databricks. This notebook assumes that you have a file already inside of DBFS that you would like to read from.

This notebook is written in **Python** so the default cell type is Python. However, you can use different languages by using the `%LANGUAGE` syntax. Python, Scala, SQL, and R are all supported.

In [2]:
# File location and type
# BDM -- changed to part_*_ as I have loaded parquet files 0000-0004  -- more data -- better lda -- I hope
file_location = "/FileStore/tables/part_r_*_fbc86a65_*.parquet"
file_type = "parquet"

# CSV options
infer_schema = "false"
first_row_is_header = "false"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)


display(df)

mid sender timestamp omid subject body folder body_cleaned concepts 1032 keith.petersen@enron.com 2001-08-03 10:52:10 <2563307.1075860881637.JavaMail.evans@thyme> RE: Sun Devil open season draft Kevin, the document looks good. I did forward to Ranelle Paladino in Steve Kirk s group to look at it from a tariff perspective.Keith -----Original Message-----From: Hyatt, Kevin Sent:	Friday, August 03, 2001 11:23 AMTo:	Petersen, Keith; Winckowski, Michele; Corman, ShelleySubject:	Sun Devil open season draftImportance:	High << File: sundevilopenseason3.doc >> Michele and Keith,	Drew asked that I send this to you to help backstop Rob Kilmer and Teb Lokey. I have incorporated their changes. We re still waiting on final rate numbers to fill in the blanks, but we re close. I d like to get this in the trade press and on TW s website on Monday 8/6. Please call me at 853-5559 if you have any comments or concerns.thanksKevin Hyatt Kevin_Hyatt_Mar2002Hyatt, KevinProjectsSun Devil List(kevin, document, look, forward, ranelle, paladino, steve, kirk, look, tariff, perspective, keith, -original, message, -from, hyatt, kevin, sent, friday, august, 2001, 11:23, amto, petersen, keith, winckowski, michele, corman, shelleysubject, sun, devil, season, draftimportance, file, sundevilopenseason3, doc, michele, keith, drew, send, help, backstop, rob, kilmer, teb, lokey, incorporated, change, waiting, final, rate, fill, blank, close, trade, press, website, monday, 8/6, please, call, 853-5559, comment, concern, thankskevin) List() 1232 info@pmaconference.com 2002-03-06 10:52:18 <3487296.1075860877232.JavaMail.evans@thyme> Power Executive-- Free Sample Issue We welcome you to download a freetrial issue of New Power Executive , the market s leading weekly on market intel, trend analysis, and a host of strategic issues and ideas of direct importance to your planning and business development process. Read by thousands of senior execs around the market, New Power Executive is has been considered a must-read publication since 1997. These four free issues you ll receive over the coming weeks are free and have zero obligation. However, if you choose to formally subscribe during this trial you can save $150 off the regular rate. See the order form on page 5. Enjoy! This email has been sent to kevin.hyatt@enron.com, by PowerMarketers.com.Visit our Subscription Center to edit your interests or unsubscribe.http://ccprod.roving.com/roving/d.jsp?p=oo&m=1000838503237&ea=kevin.hyatt@enron.comView our privacy policy: http://ccprod.roving.com/roving/CCPrivacyPolicy.jspPowered byConstant Contact(R)www.constantcontact.com Kevin_Hyatt_Mar2002Hyatt, KevinInbox List(welcome) List() 1432 kevin.hyatt@enron.com 2002-02-25 07:46:38 <8699033.1075860874683.JavaMail.evans@thyme> Pioneer Gas Pipeline Bill, I need a confidentiality agrmt for a proposed pipe sale transaction.We are evaluating possibly selling a lateral piece of TW pipe to Pioneer. They are interested in purchasing approx. 35 miles of pipe that TW took out of service in 2000. The pipe in located in Ward and Pecos County, Texas. Once the C.A. is executed, we would let Pioneer begin due diligence covering information such as easements, maintenance records, physical location, etc.Pioneer is an owner/operator of gas gathering & intrastate pipe transmission assets. Their info is as follows:Pioneer Gas Pipeline, Inc.Mr. Philip R. Allard, President502 S. Koenigheim, Suite 3ASan Angelo, Texas 76903ph 915-655-3300fax 915-655-3315let me know if you need any further info.thxKevin Hyattx35559 Kevin_Hyatt_Mar2002Hyatt, KevinSent Items List(bill, confidentiality, agrmt, proposed, pipe, sale, transaction, evaluating, possibly, selling, lateral, piece, pipe, pioneer, purchasing, approx, mile, pipe, service, 2000., pipe, located, ward, pecos, county, texas, executed, pioneer, due, diligence, covering, information, easement, maintenance, record, physical, location, etc, pioneer, owner/operator, gas, gathering, intrastate, pipe, transmission, 

In [3]:
# Create a view or table
# Change the subject text to lower case and the timestamp to a date whereby we drop the hours and minutes such
# that the format of the timestamp data is now 'YYYY-MM-DD'  -- This could be an issue as we lost hh-mm but it was only way 
# for me to get generic filter my dataframe function working to get emails by date --YYYY-MM-DD
# May have to revisit
# 
from pyspark.sql.functions import lower, col, date_format
#from pyspark.sql.functions import *
# 
df = df.select("mid","sender", date_format(col("timestamp"),'yyyy-MM-dd').alias("timestamp"), \
               "omid",lower(col('subject')).alias('subject'), "body", "folder","body_cleaned", "concepts")

temp_table_name = 'df'
df.createOrReplaceTempView('df')
#display(df)
df.count()


Out[ 2 ]: 6306

In [4]:
%sql

/* Query the created temp table in a SQL cell  Left here as an example of code syntax */

select count(*) from `df`

count(1) 6306

In [5]:
# df1 and df2 are temp dataframes containing subject with replies and forwards as it was thought
# that it might be a good idea to create a dataframe where we eliminate those emails
# no_for_or_replies is the final df that eliminated the forwards and replies
df1 = df.filter(df['subject'].startswith("re:"))
df2 = df.filter(df['subject'].startswith("fw:"))
df1.createOrReplaceTempView('df1')
df2.createOrReplaceTempView('df2')

no_for_or_replies_df = spark.sql("select * from df minus (select * from df1 union select * from df2)")
display(no_for_or_replies_df)
no_for_or_replies_df.createOrReplaceTempView('no_for_or_replies_df')


mid sender timestamp omid subject body folder body_cleaned concepts 307235 vince.kaminski@enron.com 2001-04-13 <13989990.1075856440632.JavaMail.evans@thyme> vince kaminski s \"bio\" and requirements for the siam invitation ---------------------- Forwarded by Vince J Kaminski/HOU/ECT on 04/13/2001 09:32 PM ---------------------------Shirley Crenshaw04/12/2001 09:35 PMTo: fitz@math.uh.educc: (bcc: Vince J Kaminski/HOU/ECT)Subject: Vince Kaminski s \"Bio\" and requirements for the SIAM invitationHello Professor Fitzgibbon:Attached please find a \"bio\" for Vince Kaminski. He will require an LCDprojector for his presentation.If you need anything else, please let me know.Regards,Shirley CrenshawAdministrative CoordinatorEnron Research Group713-853-5290email: Shirley.Crenshaw@enron.com---------------------- Forwarded by Shirley Crenshaw/HOU/ECT on 04/12/2001 03:30 PM ---------------------------Vince J Kaminski04/11/2001 02:17 PMTo: Shirley Crenshaw/HOU/ECT@ECTcc: Subject: SIAM invitationFYIVince---------------------- Forwarded by Vince J Kaminski/HOU/ECT on 04/11/2001 02:19 PM ---------------------------\"William Fitzgibbon\" on 03/13/2001 02:45:57 PMTo: cc: Subject: SIAM invitationDear Dr. Kaminskihere is an email invitation for teh SIAM event. A hard copy will followDr. V. KaminskiEnronP.O. Box 1188Houston, Texas 77251-1188Dear Dr. KaminskiMarch 12, 2001I am writing to formalize your invitation to attend, participate, and speakin the SIAM Southwest Regional Mathematics in Industry Workshop. A timespan of thirty minutes is being allotted to invited talks with an additionalten minutes or so for discussion. The workshop, funded under the auspicesof a National Science Foundation grant to SIAM will not be a standardapplied mathematics event with representatives from industry, academe, andgovernmental agencies presenting their latest research results. Instead themeeting will emphasize the mathematics and technology currently applied tothe projects of industry and governmental laboratories. Additionally theevent will focus upon the mechanisms facilitating interaction andcollaboration between the academy, industry, and government laboratories.The workshop will be held at the University of Houston Hilton Hotel, April27-28. Funds will be available to support both travel expenses and the costof food and lodging of invited speakers. We will be happy to make travelarrangements on this end if so desired.We hope that you can accept our invitation. If this is the case pleasefurnish us with a title, a short abstract, and a list of the necessaryequipment for your presentation.We look forward to seeing you at the University of Houston.SincerelyW. Fitzgibbon Vincent_Kaminski_Jun2001_3Notes FoldersSent List(forwarded, vince, kaminski/hou/ect, 04/13/2001, 09:32, -shirley, crenshaw04/12/2001, 09:35, pmto, fitz, math, educc, bcc, vince, kaminski/hou/ect, subject, vince, kaminski, bio, requirement, siam, invitationhello, professor, fitzgibbon, attached, please, bio, vince, kaminski, require, lcdprojector, presentation, else, please, regard, shirley, crenshawadministrative, coordinatorenron, research, group713-853-5290email, shirley, crenshaw, enron, com, forwarded, shirley, crenshaw/hou/ect, 04/12/2001, 03:30, -vince, kaminski04/11/2001, 02:17, pmto, shirley, crenshaw/hou/ect, ectcc, subject, siam, invitationfyivince, forwarded, vince, kaminski/hou/ect, 04/11/2001, 02:19, william, fitzgibbon, fitz, math, edu, 03/13/2001, 02:45:57, pmto, vkamins, enron, com, elizabet, math, edu, subject, siam, invitationdear, dr., kaminskihere, email, invitation, teh, siam, event, hard, copy, followdr, kaminskienronp, box, 1188houston, texas, 77251-1188dear, dr., kaminskimarch, 2001i, writing, formalize, invitation, attend, participate, speakin, siam, southwest, regional, mathematics, industry, workshop, timespan, thirty, minute, allotted, invited, talk, additionalten, minute, discussion, workshop, funded, auspicesof, national, science, foundation, grant, siam, standardapp

In [6]:
%sql


select count(*) from no_for_or_replies_df

count(1) 3922

In [7]:
# This creates a dataframe (only_bigrams_df) from no_for_or_replies_df above where we reduce further to eliminate any emails that do not have a bigram from 
# the concepts column
import pyspark.sql.functions as F
only_bigrams_df=spark.sql("SELECT * from no_for_or_replies_df").filter(F.size('concepts') > 0)
only_bigrams_df.createOrReplaceTempView('only_bigrams_df')  

In [8]:
%sql
select count(*) from only_bigrams_df

count(1) 1250

In [9]:
# Below is a function that is meant to clean the enron email data from text that is not useful to summarization -- thanks Marta
# I attempted to remove all puncuation except for periods but it wasnt working  -- Revisit
# We should all add to clean function as source to pre-process data
import re, html, string
rem = ['(?s)<TYPE>GRAPHIC.*?</TEXT>',
'(?s)<TYPE>EXCEL.*?</TEXT> ',
'(?s)<TYPE>PDF.*?</TEXT>',
'(?s)<TYPE>ZIP.*?</TEXT>',
'(?s)<TYPE>COVER.*?</TEXT>',
'(?s)<TYPE>CORRESP.*?</TEXT>',
'(?s)<TYPE>EX-10[01].INS.*?</TEXT>',
'(?s)<TYPE>EX-99.SDR [KL].INS.*?</TEXT>',
'(?s)<TYPE>EX-10[01].SCH.*?</TEXT>',
'(?s)<TYPE>EX-99.SDR [KL].SCH.*?</TEXT>',
'(?s)<TYPE>EX-10[01].CAL.*?</TEXT>',
'(?s)<TYPE>EX-99.SDR [KL].CAL.*?</TEXT>',
'(?s)<TYPE>EX-10[01].DEF.*?</TEXT>',
'(?s)<TYPE>EX-99.SDR [KL].LAB.*?</TEXT>',
'(?s)<TYPE>EX-10[01].LAB.*?</TEXT>',
'(?s)<TYPE>EX-99.SDR [KL].LAB.*?</TEXT>',
'(?s)<TYPE>EX-10[01].PRE.*?</TEXT>',
'(?s)<TYPE>EX-99.SDR [KL].PRE.*?</TEXT>',
'(?s)<TYPE>EX-10[01].REF.*?</TEXT>',
'(?s)<TYPE>XML.*?</TEXT>',
'<TYPE>.*',
'<SEQUENCE>.*',
'<FILENAME>.*',
'<DESCRIPTION>.*',
'(?s)(?i)<Head>.*?</Head>',
'(?s)(?i)<Table.*?</Table>',
'(?s)<[^>]*>']
#
def clean(txt):
#  txt=txt.replace (".",". ")
  doc = re.sub("\xa0|\n|\t|—|_"," ",html.unescape(txt))
  remove = string.punctuation
  remove = remove.replace(".", "") # don't remove periods
  pattern = r"[{}]".format(remove) # create the pattern
#  bdm_doc=re.sub(pattern, "", txt) 
#  return re.sub("(?s) +"," ",re.sub(rem[-1]," ",bdm_doc))
  return re.sub("(?s) +"," ",re.sub(rem[-1]," ",doc))
#
def add_space(s):
    res = re.sub('\s+$', '', re.sub('\s+', ' ', re.sub('\.', '. ', s)))
    if res[-1] != '.':
       res += '.'
    return res
def remove_punct(s):
  remove=string.punctuation
  remove=remove+'\0123456789[]'
  s.translate(None, remove)
#def remove_punct(s):
#  remove = string.punctuation
#  pattern = r"[{}]".format(remove) # create the pattern
#  return re.sub(pattern, "", s) 

In [10]:
#Generic function to filter a dataframe based on passing a dictionary 
#consisting of key - pairs as {column_name:column_value}
#This functions also requires that the name of the dataframe is passed in as well
#Could not get sql to be truly dynamic due to the sql with argument requiring a select_string.format syntax as the .format part
#is not allowed to be a string (Looked up eval, exec, set_attrib, etc) None of these would work.
#This function requires a temporary table as the dataframe and can only have a max of 3 items in dictionary and thus,
#only 3 values chanied and filtered in the where clause.
 
def filter_my_dataframe (my_dict, my_df):
#
  my_counter=0
  my_query='select * from ' + my_df + ' where '
#
# Build the select and where clause string
#
  for my_key in test_dict.keys():
    my_counter+=1
    if my_counter==1:
      my_query=my_query+my_key+'="{}"'
    else:
      my_query=my_query+' and '+my_key+'="{}"'
#  
  format_str='.format('
  my_counter=0
#
# Determine the number of passed values -- max is 3
#
  for my_value in test_dict.values():
    my_counter+=1
    if my_counter==1:
      my_first_val=my_value
    else:
      if my_counter==2:
        my_second_val=my_value
      else:
        if my_counter==3:
          my_third_val=my_value
#
# Build the format that requires appending to the select/where string as 'sql_string'.format
#
  if my_counter==1:
    my_query=my_query.format(my_first_val)
  if my_counter==2:
    my_query=my_query.format(my_first_val, my_second_val)
  if my_counter==3:
    my_query=my_query.format(my_first_val,my_second_val, my_third_val)
#
  return (sqlContext.sql(my_query))

In [11]:
# The nltk_text_summarization function was written from code set in article (https://stackabuse.com/text-summarization-with-nltk-in-python/)
# This function will return n sentences that are weighted with frequently used words for each email as an rdd/dataframe to be provided as an argument to the function
#
import nltk
import heapq
from nltk.tokenize import sent_tokenize,word_tokenize
nltk.download('punkt')
nltk.download('stopwords')
def nltk_text_summarization(my_email, my_num_of_summary_sentences):
  try:
#
# Use nltk to tokenize the sentences. Initialize the stop words and dictionat for word_frequencies
#
    sentence_list = nltk.sent_tokenize(my_email)
    stopwords = nltk.corpus.stopwords.words('english')
    word_frequencies = {}  
# 
# Load the words from email into dictionary and initialize to 1 and keep running count as value
#
    for word in nltk.word_tokenize(my_email):
      if word not in stopwords:
        if word not in word_frequencies.keys():
          word_frequencies[word] = 1
        else:
          word_frequencies[word] += 1
#
# weight the word counts by dividing by the maximum word count found in the email
#
    maximum_frequency = max(word_frequencies.values())
    for word in word_frequencies.keys():
      word_frequencies[word] = (word_frequencies[word]/maximum_frequency)
#
# Find the sentences and add word frequency weights to the sentences in a dictionary structure.
# This will identify the sentences that have the highest word weights that will be used for the text summary
#
    sentence_scores = {}
    for sent in sentence_list:
      for word in nltk.word_tokenize(sent.lower()):
        if word in word_frequencies.keys():
          if len(sent.split(' ')) < 30:
            if sent not in sentence_scores.keys():
              sentence_scores[sent] = word_frequencies[word]
            else:
              sentence_scores[sent] += word_frequencies[word]
# 
# Store the count of the number of sentences in the email 
# If the sentence length is < 3 , then use all sentences for the text summary
# Else capture the top N sentences specified in the call to function to be used for the text summary
#
    the_length=len(sentence_scores)
    if the_length < my_num_of_summary_sentences:
      summary_sentences = heapq.nlargest(the_length, sentence_scores, key=sentence_scores.get)
    else:
      summary_sentences = heapq.nlargest(my_num_of_summary_sentences, sentence_scores, key=sentence_scores.get)
    my_summary = ' '.join(summary_sentences)
    return(my_summary)
  except:
    pass

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data] Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data] Unzipping corpora/stopwords.zip.

In [12]:
num_of_summary_sentences=3
my_nltk_df = no_for_or_replies_df.select('mid','body').rdd.map(lambda x:(x[0],nltk_text_summarization(clean(str(x[1]).replace("."," ")),num_of_summary_sentences))) \
           .filter(lambda x: x[1]).filter(lambda x: x[1] is not None)
#big_test.collect()
#   .filter(lambda x: x).filter(lambda x: x is not None)
my_nltk_df1 = my_nltk_df.toDF(['mid','summary'])
my_nltk_df1.createOrReplaceTempView('my_nltk_df1')  

In [13]:
num_of_summary_sentences=3
my_nltk_df = no_for_or_replies_df.select('mid','body').rdd.map(lambda x:(x[0],nltk_text_summarization(clean(str(x[1])),num_of_summary_sentences))) \
           .filter(lambda x: x[1]).filter(lambda x: x[1] is not None)
#big_test.collect()
#   .filter(lambda x: x).filter(lambda x: x is not None)
my_nltk_df1 = my_nltk_df.toDF(['mid','summary'])
my_nltk_df1.createOrReplaceTempView('my_nltk_df1')    

In [14]:
%sql select * from my_nltk_df1

mid summary 307235 Box 1188Houston, Texas 77251-1188Dear Dr. KaminskiMarch 12, 2001I am writing to formalize your invitation to attend, participate, and speakin the SIAM Southwest Regional Mathematics in Industry Workshop. Additionally theevent will focus upon the mechanisms facilitating interaction andcollaboration between the academy, industry, and government laboratories.The workshop will be held at the University of Houston Hilton Hotel, April27-28. Instead themeeting will emphasize the mathematics and technology currently applied tothe projects of industry and governmental laboratories. 333234 I also made a change to May. I was calculating the differential off of the wrong location index.DG Drew,Here is Agave for June. 384232 are you coming to the uh/tx game on 9/23 - is donnita? 126632 Thanks. 108233 You can check the progress of your request by clicking http://itcapps.corp.enron.com/srrs/auth/emailLink.asp?ID=000000000020857&Page=MyReq. You will be notified by email when your request has been processed. Thank you for your request. 360634 Rita, In order to book the imbalance payback between HPL and Lobo, I have created deal 1166748 (ENA selling to AEP @ $2.45). Following that, we sold the gas to the central desk, who sold it to Oneok at the South Texas pool. With the changes I made and the entries you are able to do, hopefully this deal will be wrapped up. 213032 ?$684.65 [IMAGE][IMAGE]HipZip MP3 Player Kit USB w/2 40MB Disk, Head Phones By Iomega Get a $50 Rebate direct from Iomega from February 17, 2001 through June 30, 2001. ?$135.27 [IMAGE][IMAGE]Stylus Color 777 Ink Jet 2880x720 12ppm USB By Epson The EPSON Stylus Color 777 ink jet printer delivers remarkable print speed, superb output and outstanding value. ?$505.64 [IMAGE][IMAGE]ML591 24-Pin 120V 360CPS Wide Parallel By Okidata Microline 590 and 591 OKISMART Paper Handling for hassle-free, reliable switching between different media. 109631 > Tracy Ross, Counsel, Royal Bank of CanadaPhone: 416-974-5503; Fax: 416-974-2217File - This email may be privileged and confidential.? Any dissemination or use of this information by a person other than the intended recipient(s) is unauthorized.? Attached is the language that is necessary to make sure the CSA is one way.? 247831 Send to SSchneider@aep.com with a copy to MLCarriere@aep.com. Please forward your altered draft back to me when completed. 272832 ----------------------------------------------------------------------------------This message and any attachments (the \"message\") are intended solely for the addressees and are confidential. X-FileName: dutch quigley 6-26-02.PST(See attached file: Delta11-28.xls) Ce message et toutes les pieces jointes (ci-apres le \"message\") sont etablis a l intention exclusive de ses destinataires et sont confidentiels. BNP PARIBAS (and its subsidiaries) shall (will) not therefore be liable for the message if modified. 268035 X-FileName: holden salisbury 6-26-02.PSTHello,Could you please remove me from this email list.Thank You 335632 We need to let people and companies that the address has changed.D I just cancelled it. 72631 ---------------------- Forwarded by Suzanne Vann/HOU/EES on 10/16/2001 01:36 PM ---------------------------EES Product Announcement10/16/2001 10:42 AMSent by: Kathleen Pope-SanceTo: All EEScc: Subject: NEW! We then sell that displaced power on the wholesale market--where the prices are high--and share the revenue with the customer. Enron monitors the wholesale power market, and when prices spike, we notify our customers to operate their on-sitegenerators. 39035 One, Socal CA production/Socal storage/EPNG Ehrenberg, Two, Topock TW and EPNG, Three, KRS/Wheeler Ridge. Remember, Socal is an island, not because of the delivered capacity to the border via EPNG and TW, but because of the limited capacity of Socal s interconnects. Picture the market, San Juan gas is trading well below the Permian and Waha basins, which happen to be the marginal supply points for the west

In [15]:
# Below shows a test of a generic function created to filter a dataframe.  
# The function filter_my_dataframe can be used to compund your where clause via a dictionary you create for your columns in the where clause
# The function dynamically builds the where clause via parameters passed via dictionary for where clause. The second parameter is the name of the dataframe
# Belows test grabs an email via message id , mid, but can also be used to grab a certain date as well as a spcific sender
#
#test_dict={'mid':404632}
test_dict={'mid':68633}
#test_dict={'sender':'ken.skilling@enron.com'}
test_df='df'
test_a_row=filter_my_dataframe(test_dict,test_df)
#type(test_a_row)
t=test_a_row.select('body').collect()
#t=test_a_row.select 'body'.rdd
#mi=nltk_text_summarization(clean(str(t)))
#my_weight_frequency(mi)
#nltk_text_summarization(clean(str(t)))
sum_sentences=nltk_text_summarization(clean(str(t)),3)
print(sum_sentences)


In fact, EnronOnline trading volumes are currently experiencing above-normal activity.We will continue to update you as new developments arise. We expected this, because it is not unusual to be downgraded after using assets to secure credit. This is still above investment grade.The ratings of our pipelines Northern Natural Gas and Transwestern have also been lowered from A- to BBB.

In [16]:
%sql select body from no_for_or_replies_df where mid=68633

body Following our announcement of an additional of $1 billion credit line, Standard & Poor s (S&P) today downgraded Enron s long-term credit rating one notch from BBB+ to BBB and short-term rating from A2 to A3. We expected this, because it is not unusual to be downgraded after using assets to secure credit. This is still above investment grade.The ratings of our pipelines Northern Natural Gas and Transwestern have also been lowered from A- to BBB. In S&P s words, \"Their ratings [are now] in line with those of the parent company to reflect S&P s view that Enron s pipeline assets have become more strategic to the company.\"S&P also said, \"[We continue] to believe that Enron s liquidity position is adequate to see the company through the current period of uncertainty, and that the company is working to provide itself with an even greater liquidity cushion through additional bank lines and pending asset sales.\"As I ve said before, building on our liquidity position through additional credit lines maintains our counterparties confidence and strengthens our core businesses.It s important for you to know that our gas and power numbers - which account for more than 95 percent of our trading activity - indicate that our customer base is not withdrawing, closing out positions, or reducing transaction levels as a result of credit concerns. In fact, EnronOnline trading volumes are currently experiencing above-normal activity.We will continue to update you as new developments arise. Thank you.

In [17]:
from gensim.summarization.summarizer import summarize
import re
import nltk
from nltk.tokenize import sent_tokenize,word_tokenize


def short(sent):
  try:
    return summarize(sent)
  except:
    pass


In [18]:
body_clean = no_for_or_replies_df.select('mid','body') \
   .rdd.map(lambda x:(x[0],short(re.sub(r'[^a-zA-Z\s\.]', ' ',clean(str(x[1])))))) \
   .filter(lambda x: x[1]).filter(lambda x: x[1] is not None)
body_clean1 = body_clean.toDF(['mid','summary'])
body_clean1.createOrReplaceTempView('body_clean1')  

In [19]:
%sql

SELECT * FROM body_clean1 where summary <> "";

mid summary 307235 KaminskiEnronP.O. Box Houston Texas Dear Dr. KaminskiMarch I am writing to formalize your invitation to attend participate and speakin the SIAM Southwest Regional Mathematics in Industry Workshop.
The workshop funded under the auspicesof a National Science Foundation grant to SIAM will not be a standardapplied mathematics event with representatives from industry academe andgovernmental agencies presenting their latest research results. 360634 . From what I understand we received the gas at King Ranch sold it to AEP so that they would move it through the header on their contract and bought it back at a half cent difference. 213032 IMAGE June Can t read this email Click hereIssue e PROVANTAGE Customer jeff dasovich enron.comTo unsubscribe from the Original Advantage Click here Do Not Reply to this email Products that give you the Professional Advantage IMAGE Crystal Reports v .
IMAGE IMAGE PhotoSmart xi Digital Camera .
IMAGE IMAGE MB Smart Media Card .
IMAGE IMAGE PYRO CardBus DV for Notebooks By ADS Technologies Add IEEE ports to your Notebook Capture and Edit Digital Video Transfer data at Mb Sec. Connect to Hard Drives Printers Scanners ...More .
GB External FireWire Dr By QPS Inc. The Que DVD RAM Fire Drive is ideal for desktop publishing archiving and presentations.
IMAGE Web Address www.PROVANTAGE.com Toll Free Fax email sales provantage.com Privacy Policy Terms Conditions FREE Catalog PROVANTAGE Corporation Whipple Ave. NW North Canton OH Products prices terms conditions or offers may change at any time.
The Original Advantage promotional email is delivered only to customers of PROVANTAGE Corporation.
PROVANTAGE customers have purchased products in the past and submitted their email address as part of the checkout process. 272832 X FileName dutch quigley .PST See attached file Delta .xls Ce message et toutes les pieces jointes ci apres le message sont etablis a l intention exclusive de ses destinataires et sont confidentiels. 72631 We then sell that displaced power on the wholesale market where the prices are high and share the revenue with the customer. 39035 Topock is a more liquid market because of the upstream transport contracts on EPNG and downstream buying patterns of certain Socal markets.
Picture the market San Juan gas is trading well below the Permian and Waha basins which happen to be the marginal supply points for the west.
Because of the of the limited capacity going into Socal Topock every transporter on EPNG and TW wants to fill their contracts with San Juan gas first.
This transport leg simply displaces Permian gas going into Plains North and allows Permian gas to head west to Ehrenberg on the EPNG south mainline.
When demand exceeds all available historical supply points and begins to reach to Waha to meet Ehrenberg demand you have a paradigm shift.
When Keystone West reaches maximum capacity the rule of market spreads not exceeding the max rate transport rate then dies a fast death.
There is simply no available capacity at the Keystone West meter to allow a shipper to buy max rate transport on EPNG and ship it to Socal.
The supply exists but there isn t enough refining capacity available to meet demand. 127431 The price does not include line losses which the Company agreed to throw in if another marketer signs on none did The market price is also the shopping credit.
The shopping credit for residential and commercial customers is low but could possibly work pending analysis from structuring.
. Customers on special contracts approximately of them can during the first year either opt to cancel their contract or extend it through the RTC recovery period which is unlawful in my view although that observation did not slow anyone down.
. The settlement creates an implicit cap on shopping of since the Company will seek to have the incentive removed once the is reached.
billion without quantification or review are Consumers Counsel Staff Industrial Users Retail Merchants Low income some Ohio

In [20]:
df_lda = spark.sql("select a.*, b.summary from no_for_or_replies_df a, body_clean1 b \
where a.mid=b.mid and b.summary<>\'\'").rdd
df_lda.take(5)

Out[ 11 ]: 
[Row(mid=307235, sender='vince.kaminski@enron.com', timestamp='2001-04-13', omid='<13989990.1075856440632.JavaMail.evans@thyme>', subject='vince kaminski s \\"bio\\" and requirements for the siam invitation', body='---------------------- Forwarded by Vince J Kaminski/HOU/ECT on 04/13/2001 09:32 PM ---------------------------Shirley Crenshaw04/12/2001 09:35 PMTo: fitz@math.uh.educc: (bcc: Vince J Kaminski/HOU/ECT)Subject: Vince Kaminski s \\"Bio\\" and requirements for the SIAM invitationHello Professor Fitzgibbon:Attached please find a \\"bio\\" for Vince Kaminski. He will require an LCDprojector for his presentation.If you need anything else, please let me know.Regards,Shirley CrenshawAdministrative CoordinatorEnron Research Group713-853-5290email: Shirley.Crenshaw@enron.com---------------------- Forwarded by Shirley Crenshaw/HOU/ECT on 04/12/2001 03:30 PM ---------------------------Vince J Kaminski04/11/2001 02:17 PMTo: Shirley Crenshaw/HOU/ECT@ECTcc: Subject: SIAM invitationFYIVince---------------------- Forwarded by Vince J Kaminski/HOU/ECT on 04/11/2001 02:19 PM ---------------------------\\"William Fitzgibbon\\" <fitz@math.uh.edu> on 03/13/2001 02:45:57 PMTo: <vkamins@enron.com>cc: <elizabet@math.uh.edu> Subject: SIAM invitationDear Dr. Kaminskihere is an email invitation for teh SIAM event. A hard copy will followDr. V. KaminskiEnronP.O. Box 1188Houston, Texas 77251-1188Dear Dr. KaminskiMarch 12, 2001I am writing to formalize your invitation to attend, participate, and speakin the SIAM Southwest Regional Mathematics in Industry Workshop. A timespan of thirty minutes is being allotted to invited talks with an additionalten minutes or so for discussion. The workshop, funded under the auspicesof a National Science Foundation grant to SIAM will not be a standardapplied mathematics event with representatives from industry, academe, andgovernmental agencies presenting their latest research results. Instead themeeting will emphasize the mathematics and technology currently applied tothe projects of industry and governmental laboratories. Additionally theevent will focus upon the mechanisms facilitating interaction andcollaboration between the academy, industry, and government laboratories.The workshop will be held at the University of Houston Hilton Hotel, April27-28. Funds will be available to support both travel expenses and the costof food and lodging of invited speakers. We will be happy to make travelarrangements on this end if so desired.We hope that you can accept our invitation. If this is the case pleasefurnish us with a title, a short abstract, and a list of the necessaryequipment for your presentation.We look forward to seeing you at the University of Houston.SincerelyW. Fitzgibbon', folder='Vincent_Kaminski_Jun2001_3Notes FoldersSent', body_cleaned=['forwarded', 'vince', 'kaminski/hou/ect', '04/13/2001', '09:32', '-shirley', 'crenshaw04/12/2001', '09:35', 'pmto', 'fitz', 'math', 'educc', 'bcc', 'vince', 'kaminski/hou/ect', 'subject', 'vince', 'kaminski', 'bio', 'requirement', 'siam', 'invitationhello', 'professor', 'fitzgibbon', 'attached', 'please', 'bio', 'vince', 'kaminski', 'require', 'lcdprojector', 'presentation', 'else', 'please', 'regard', 'shirley', 'crenshawadministrative', 'coordinatorenron', 'research', 'group713-853-5290email', 'shirley', 'crenshaw', 'enron', 'com', 'forwarded', 'shirley', 'crenshaw/hou/ect', '04/12/2001', '03:30', '-vince', 'kaminski04/11/2001', '02:17', 'pmto', 'shirley', 'crenshaw/hou/ect', 'ectcc', 'subject', 'siam', 'invitationfyivince', 'forwarded', 'vince', 'kaminski/hou/ect', '04/11/2001', '02:19', 'william', 'fitzgibbon', 'fitz', 'math', 'edu', '03/13/2001', '02:45:57', 'pmto', 'vkamins', 'enron', 'com', 'elizabet', 'math', 'edu', 'subject', 'siam', 'invitationdear', 'dr.', 'kaminskihere', 'email', 'invitation', 'teh', 'siam', 'event', 'hard', 'copy', 'followdr', 'kaminskienronp', 'box', '1188houston', 'texas', '77251-1188dear', 'dr.', 'kaminskimarch', '2001i', 'wr

In [21]:
df_lda = spark.sql("SELECT * FROM body_clean1 where summary <> \'\'").rdd.map(lambda x: (x[1],x[0]))
print(type(df_lda))
df_lda.collect()

<class 'pyspark.rdd.PipelinedRDD'>
 Out[ 68 ]: 
[('KaminskiEnronP.O. Box Houston Texas Dear Dr. KaminskiMarch I am writing to formalize your invitation to attend participate and speakin the SIAM Southwest Regional Mathematics in Industry Workshop.\nThe workshop funded under the auspicesof a National Science Foundation grant to SIAM will not be a standardapplied mathematics event with representatives from industry academe andgovernmental agencies presenting their latest research results.',
 307235),
 ('. From what I understand we received the gas at King Ranch sold it to AEP so that they would move it through the header on their contract and bought it back at a half cent difference.',
 360634),
 ('IMAGE June Can t read this email Click hereIssue e PROVANTAGE Customer jeff dasovich enron.comTo unsubscribe from the Original Advantage Click here Do Not Reply to this email Products that give you the Professional Advantage IMAGE Crystal Reports v .\nIMAGE IMAGE PhotoSmart xi Digital Camera .\nIMAGE IMAGE MB Smart Media Card .\nIMAGE IMAGE PYRO CardBus DV for Notebooks By ADS Technologies Add IEEE ports to your Notebook Capture and Edit Digital Video Transfer data at Mb Sec. Connect to Hard Drives Printers Scanners ...More .\nGB External FireWire Dr By QPS Inc. The Que DVD RAM Fire Drive is ideal for desktop publishing archiving and presentations.\nIMAGE Web Address www.PROVANTAGE.com Toll Free Fax email sales provantage.com Privacy Policy Terms Conditions FREE Catalog PROVANTAGE Corporation Whipple Ave. NW North Canton OH Products prices terms conditions or offers may change at any time.\nThe Original Advantage promotional email is delivered only to customers of PROVANTAGE Corporation.\nPROVANTAGE customers have purchased products in the past and submitted their email address as part of the checkout process.',
 213032),
 ('X FileName dutch quigley .PST See attached file Delta .xls Ce message et toutes les pieces jointes ci apres le message sont etablis a l intention exclusive de ses destinataires et sont confidentiels.',
 272832),
 ('We then sell that displaced power on the wholesale market where the prices are high and share the revenue with the customer.',
 72631),
 ('Topock is a more liquid market because of the upstream transport contracts on EPNG and downstream buying patterns of certain Socal markets.\nPicture the market San Juan gas is trading well below the Permian and Waha basins which happen to be the marginal supply points for the west.\nBecause of the of the limited capacity going into Socal Topock every transporter on EPNG and TW wants to fill their contracts with San Juan gas first.\nThis transport leg simply displaces Permian gas going into Plains North and allows Permian gas to head west to Ehrenberg on the EPNG south mainline.\nWhen demand exceeds all available historical supply points and begins to reach to Waha to meet Ehrenberg demand you have a paradigm shift.\nWhen Keystone West reaches maximum capacity the rule of market spreads not exceeding the max rate transport rate then dies a fast death.\nThere is simply no available capacity at the Keystone West meter to allow a shipper to buy max rate transport on EPNG and ship it to Socal.\nThe supply exists but there isn t enough refining capacity available to meet demand.',
 39035),
 ('The price does not include line losses which the Company agreed to throw in if another marketer signs on none did The market price is also the shopping credit.\nThe shopping credit for residential and commercial customers is low but could possibly work pending analysis from structuring.\n. Customers on special contracts approximately of them can during the first year either opt to cancel their contract or extend it through the RTC recovery period which is unlawful in my view although that observation did not slow anyone down.\n. The settlement creates an implicit cap on shopping of since the Company will seek to have the incentive removed once the is reached.\nbillion without quantifi

In [22]:
%sql
select count(*) from body_clean1 where summary is null


count(1) 0

In [23]:
%sql select a.*, b.summary as gensim_summary, c.summary as nltk_summary from no_for_or_replies_df a, body_clean1 b, my_nltk_df1 c where a.mid=b.mid and a.mid=c.mid

mid sender timestamp omid subject body folder body_cleaned concepts gensim_summary nltk_summary 189434 danny.mccarty@enron.com 2000-10-30 <5689810.1075844275312.JavaMail.evans@thyme> trailblazer expansion Rod, Who is watching over this in your shop? I d like to make sure Finance is in the loop.Dan---------------------- Forwarded by Danny McCarty/ET&S/Enron on 10/31/2000 07:58 AM ---------------------------Mike McGowan10/30/2000 05:13 PMTo: Danny McCarty/ET&S/Enron@Enroncc: Subject: Trailblazer ExpansionDan -Attached from Trailblazer is a Resolution for execution which approves various aspects of the proposed expansion. The issues and the recommendations are those which I have reviewed and agree with. They are also the exact same as the information I sent previously to you for review. There is nothing new. Are you OK with me executing these??????Also, I am working on another financing option with Kinder-Morgan which would basically increase Trailblazer s debt structure (partly in preparation of the next rate case in 2003) which would result in increased cash distribution to the partnersa in 2001. This cas could then be used to fund our cash call for the equity financing(30%) of the expansion. There would be a timing difference - we would get increased cash distributions in 2001, and then have to make our cash call in 2002 for appr. the same amount. I will develop this in more detail later this week.Let me know of any concerns.Mike McGowan---------------------- Forwarded by Mike McGowan/ET&S/Enron on 10/30/2000 06:04 PM ---------------------------\"Brown, Ronald\" on 10/30/2000 04:58:45 PMTo: \" mmcgowa@enron.com \" , \"McElligott, James\" , \" scott.hobbs@coastalcorp.com \" cc: Subject: Trailblazer ExpansionAttached is a Management Committee Resolution approving the information thatwas included in the package that was forwarded to each of you earlier in themonth. Please sign for your respective companies and return the original tome and I will forward copies of all member s signatures to each party. Ifyou have any questions, please call me on (713)369-9290. Thanks Ron < > - TB unanimous consent1.doc Rodney_Hayslett_Dec2000Notes FoldersAction items in List(rod, watching, shop, finance, loop, dan, forwarded, danny, mccarty/et, s/enron, 10/31/2000, 07:58, -mike, mcgowan10/30/2000, 05:13, pmto, danny, mccarty/et, s/enron, enroncc, subject, trailblazer, expansiondan, -attached, trailblazer, resolution, execution, approves, various, aspect, proposed, expansion, issue, recommendation, reviewed, agree, exact, information, sent, previously, review, executing, financing, option, kinder-morgan, basically, increase, trailblazer, debt, structure, partly, preparation, rate, 2003, result, increased, cash, distribution, partnersa, 2001., ca, fund, cash, call, equity, financing, expansion, timing, difference, increased, cash, distribution, 2001, cash, call, 2002, appr, amount, develop, detail, week, concern, mike, mcgowan, forwarded, mike, mcgowan/et, s/enron, 10/30/2000, 06:04, brown, ronald, ronald, brown, kindermorgan, com, 10/30/2000, 04:58:45, pmto, mmcgowa, enron, com, mmcgowa, enron, com, mcelligott, james, james, mcelligott, kindermorgan, com, scott, hobbs, coastalcorp, com, scott, hobbs, coastalcorp, com, subject, trailblazer, expansionattached, management, committee, resolution, approving, information, thatwas, included, package, forwarded, earlier, themonth, please, sign, respective, company, return, original, tome, forward, copy, signature, party, ifyou, question, please, call, 713, 369-9290., ron, unanimous, consent1, doc, unanimous, consent1) List() Rod Who is watching over this in your shop I d like to make sure Finance is in the loop.Dan Forwarded by Danny McCarty ET S Enron on AM Mike McGowan PMTo Danny McCarty ET S Enron Enroncc Subject Trailblazer ExpansionDan Attached from Trailblazer is a Resolution for execution which approves various aspects of the proposed expansion.
I will develop this in more detail later this week.Let

In [24]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from gensim.parsing.porter import PorterStemmer
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np
np.random.seed(2018)
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Unzipping corpora/wordnet.zip.
 Out[ 13 ]: True

In [25]:
def lemmatize_stemming(text):
  stemmer = PorterStemmer()
  return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))
def lemstem_preprocess(text):
  result = []
  for token in gensim.utils.simple_preprocess(text):
    if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
      result.append(lemmatize_stemming(token))
  return result

In [26]:
df.count()
test_dict={'mid':68633}
test_df='df'
test_a_row=filter_my_dataframe(test_dict,test_df)
#t=test_a_row.select('body','mid').collect()
#t=test_a_row.select('body')
#t=test_a_row.select('body','mid')
#type(t)
#print(t)
#t=no_for_or_replies_df.select ('body','mid').collect() 
t=spark.sql ("select body from no_for_or_replies_df")
#type(t.collect())
#type(t.take(1))
processed_email =t.rdd.flatMap(lambda x:lemstem_preprocess(clean(str(x)))).collect()
#processed_email =t.rdd.flatMap(lambda x:(lemstem_preprocess(clean(str(x[1]))),x[0])).collect()
dictionary = gensim.corpora.Dictionary(processed_email)
processed_email.take(5)





--------------------------------------------------------------------------- 
 TypeError Traceback (most recent call last)
 <command-2430134850374733> in <module> () 
 14 processed_email = t . rdd . flatMap ( lambda x : lemstem_preprocess ( clean ( str ( x ) ) ) ) . collect ( ) 
 15 #processed_email =t.rdd.flatMap(lambda x:(lemstem_preprocess(clean(str(x[1]))),x[0])).collect() 
 ---> 16 dictionary = gensim . corpora . Dictionary ( processed_email ) 
 17 processed_email . take ( 5 ) 
 18 

 /databricks/python/lib/python3.5/site-packages/gensim/corpora/dictionary.py in __init__ (self, documents, prune_at) 
 81 
 82 if documents is not None : 
 ---> 83 self . add_documents ( documents , prune_at = prune_at ) 
 84 
 85 def __getitem__ ( self , tokenid ) : 

 /databricks/python/lib/python3.5/site-packages/gensim/corpora/dictionary.py in add_documents (self, documents, prune_at) 
 200 
 201 # update Dictionary with the document 
 --> 202 self . doc2bow ( document , allow_update = True ) # ignore the result, here we only care about updating token ids 
 203 
 204 logger.info(

 /databricks/python/lib/python3.5/site-packages/gensim/corpora/dictionary.py in doc2bow (self, document, allow_update, return_missing) 
 238 """
 239 if isinstance ( document , string_types ) : 
 --> 240 raise TypeError ( "doc2bow expects an array of unicode tokens on input, not a single string" ) 
 241 
 242 # Construct (word, frequency) mapping. 

 TypeError : doc2bow expects an array of unicode tokens on input, not a single string

In [27]:
#test_dict={'mid':68633}
#test_df='df'
#test_a_row=filter_my_dataframe(test_dict,test_df)
#t=test_a_row.select('body','mid').collect()
#t=test_a_row.select('body','mid')
#type(t)
#print(t)
t = df.select('body_cleaned').rdd.map(lambda x:x.asList()).take(5)
print(t)



--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-3160152185314837> in <module> () 
 6 #type(t) 
 7 #print(t) 
 ----> 8 t = df . select ( 'body_cleaned' ) . rdd . map ( lambda x : x . asList ( ) ) . take ( 5 ) 
 9 print ( t ) 
 10 

 NameError : name 'df' is not defined

In [28]:
t=spark.sql ("select body_clean from df").collect()
stemmer = PorterStemmer()
process_email= 
words = []
for word in clean(str(t[0])).split(' '):
    words.append(word)
print(words)
for token in gensim.utils.simple_preprocess(clean(str(t[0]))):
  print(token)
  print(lemmatize_stemming(token))
  
from pyspark.sql import SQLContext, Row
from pyspark.ml.feature import CountVectorizer
from pyspark.mllib.clustering import LDA, LDAModel
from pyspark.mllib.linalg import Vector, Vectors

# Loads data.
data = df_lda.rdd.map(lambda (words,idd): Row(idd = idd, words = words.split(" ")))
#data.count()
docDF = spark.createDataFrame(data)
Vector = CountVectorizer(inputCol="words", outputCol="vectors")
model = Vector.fit(docDF)
result = model.transform(docDF)

corpus = result.select("idd", "vectors").rdd.map(lambda x,y: [x,Vectors.fromML(y)]).cache()

# Cluster the documents into three topics using LDA
ldaModel = LDA.train(corpus, k=3,maxIterations=100,optimizer='online')
topics = ldaModel.topicsMatrix()
vocabArray = model.vocabulary

wordNumbers = 10  # number of words per topic
topicIndices = sc.parallelize(ldaModel.describeTopics(maxTermsPerTopic = wordNumbers))

def topic_render(topic):  # specify vector id of words to actual words
    terms = topic[0]
    result = []
    for i in range(wordNumbers):
        term = vocabArray[terms[i]]
        result.append(term)
    return result

topics_final = topicIndices.map(lambda topic: topic_render(topic)).collect()

for topic in range(len(topics_final)):
    print ("Topic" + str(topic) + ":")
    for term in topics_final[topic]:
        print (term)
    print ('\n')


File "<command-721104608375546>" , line 7 
 data = df_lda.rdd.map(lambda (words,idd): Row(idd = idd, words = words.split(" "))) 
 ^ 
 SyntaxError : invalid syntax

In [29]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator

# Loads data.
dataset = spark.read.format("libsvm").load("data/mllib/sample_kmeans_data.txt")

# Trains a k-means model.
kmeans = KMeans().setK(2).setSeed(1)
model = kmeans.fit(dataset)

# Make predictions
predictions = model.transform(dataset)

# Evaluate clustering by computing Silhouette score
evaluator = ClusteringEvaluator()

silhouette = evaluator.evaluate(predictions)
print("Silhouette with squared euclidean distance = " + str(silhouette))

# Shows the result.
centers = model.clusterCenters()
print("Cluster Centers: ")
for center in centers:
    print(center)